In [6]:
# %pip install --upgrade openai

In [7]:
import pandas as pd
import os
import openai
import re
import random
import yaml

# --- Configuration ---
INPUT_TSV_FILE = 'Sentence-pairs-English-Mandarin-2025-04-24.tsv'  # Replace with your input TSV file name
OUTPUT_TSV_FILE = 'filtered_output.tsv'
AUDIO_OUTPUT_DIR = 'audio'
CHINESE_CHAR_THRESHOLD = 20
# List of available OpenAI voices (choose from these)
# See https://platform.openai.com/docs/guides/text-to-speech/Voices
OPENAI_VOICES = ["alloy", "echo", "fable", "onyx", "nova", "shimmer"]

# --- Helper Function to count Chinese characters ---
def count_chinese_characters(text):
    """Counts the number of Chinese characters in a string."""
    # This regex matches a broad range of Unicode characters considered Chinese
    # (Common, Extension A, Extension B, etc.)
    return len(text)

# --- Main Processing Logic ---
def process_tsv_and_generate_audio(input_tsv, output_tsv, audio_dir, threshold, voices):
    """
    Reads TSV, filters rows, generates audio using OpenAI API, and saves results.
    """
    # Ensure audio directory exists
    os.makedirs(audio_dir, exist_ok=True)

    # Read the TSV file
    # Assuming the format is ID \t English_text \t Number \t Chinese_text
    try:
        df = pd.read_csv(input_tsv, sep='\t', header=None, names=['ID', 'English_text', 'Number', 'Chinese_text'],on_bad_lines='skip', encoding='utf-8')
        print(f"Successfully read {input_tsv}")
        print(f"Initial number of rows: {len(df)}")
    except FileNotFoundError:
        print(f"Error: Input file '{input_tsv}' not found.")
        return
    except Exception as e:
        print(f"Error reading TSV file: {e}")
        return

    # Filter rows based on Chinese character count
    df['chinese_char_count'] = df['Chinese_text'].apply(count_chinese_characters)
    filtered_df = df[df['chinese_char_count'] > threshold].copy() # Use .copy() to avoid SettingWithCopyWarning
    print(f"Number of rows after filtering (Chinese chars > {threshold}): {len(filtered_df)}")

    #filtered_df = filtered_df.head(4)
    # Add columns for audio file paths
    filtered_df['English_audio_path'] = ''
    filtered_df['Chinese_audio_path'] = ''

    # Process filtered rows and generate audio
    print("Generating audio for filtered rows...")
    for index, row in filtered_df.iterrows():
        row_id = row['ID']
        english_text = row['English_text']
        chinese_text = row['Chinese_text']

        english_audio_filename = f"en-{row_id}.wav"
        chinese_audio_filename = f"cn-{row_id}.wav"

        english_audio_path = os.path.join(audio_dir, english_audio_filename)
        chinese_audio_path = os.path.join(audio_dir, chinese_audio_filename)

        # Randomly select a voice
        selected_voice = random.choice(voices)

        try:
            # Generate English audio
            print(f"  Generating English audio for ID {row_id}...")
            english_response = openai.audio.speech.create(
                model="tts-1",  # or "tts-1-hd"
                voice=selected_voice,
                input=str(english_text) # Ensure input is a string
            )
            english_response.stream_to_file(english_audio_path)

            # Generate Chinese audio
            print(f"  Generating Chinese audio for ID {row_id}...")
            chinese_response = openai.audio.speech.create(
                model="tts-1", # or "tts-1-hd"
                voice=selected_voice, # You can use the same voice or choose another
                input=str(chinese_text) # Ensure input is a string
            )
            chinese_response.stream_to_file(chinese_audio_path)

            # Store the audio file paths in the DataFrame
            filtered_df.loc[index, 'English_audio_path'] = english_audio_path
            filtered_df.loc[index, 'Chinese_audio_path'] = chinese_audio_path

        except openai.APIError as e:
            print(f"  OpenAI API error for ID {row_id}: {e}")
            print(f"  Skipping audio generation for ID {row_id}.")
            # Optionally, you could remove this row from the filtered_df here
            # or leave the audio paths empty.
        except Exception as e:
             print(f"  An unexpected error occurred for ID {row_id}: {e}")
             print(f"  Skipping audio generation for ID {row_id}.")

    # Save the filtered DataFrame with audio paths to a new TSV file
    # Select relevant columns for the output file
    output_columns = ['ID', 'English_text', 'Number', 'Chinese_text', 'English_audio_path', 'Chinese_audio_path']
    filtered_df[output_columns].to_csv(output_tsv, sep='\t', index=False)

    print(f"\nProcessing complete.")
    print(f"Filtered data saved to '{output_tsv}'")
    print(f"Audio files saved to the '{audio_dir}' directory.")

# --- Run the process ---
if __name__ == "__main__":
    # Set your OpenAI API key (make sure you have it set as an environment variable)
    # os.environ['OPENAI_API_KEY'] = 'YOUR_ACTUAL_OPENAI_API_KEY' # Uncomment and set if not using environment variable
    # Read the YAML file
    with open('./../../Curify/curify_api.yaml', 'r') as yaml_file:
        data = yaml.safe_load(yaml_file)

    openai_api_key = data.get('openai').get('api_key')

    os.environ["OPENAI_API_KEY"] = openai_api_key

    if os.getenv('OPENAI_API_KEY') is None:
        print("Error: OPENAI_API_KEY environment variable not set.")
        print("Please set your API key before running the script.")
    else:
        process_tsv_and_generate_audio(
            INPUT_TSV_FILE,
            OUTPUT_TSV_FILE,
            AUDIO_OUTPUT_DIR,
            CHINESE_CHAR_THRESHOLD,
            OPENAI_VOICES
        )

Successfully read Sentence-pairs-English-Mandarin-2025-04-24.tsv
Initial number of rows: 70997
Number of rows after filtering (Chinese chars > 20): 3129
Generating audio for filtered rows...
  Generating English audio for ID 1280...
  Generating Chinese audio for ID 1280...
  Generating English audio for ID 1305...
  Generating Chinese audio for ID 1305...
  Generating English audio for ID 1347...
  Generating Chinese audio for ID 1347...
  Generating English audio for ID 1355...
  Generating Chinese audio for ID 1355...
  Generating English audio for ID 1377...
  Generating Chinese audio for ID 1377...
  Generating English audio for ID 1382...
  Generating Chinese audio for ID 1382...
  Generating English audio for ID 1401...
  Generating Chinese audio for ID 1401...
  Generating English audio for ID 1412...
  Generating Chinese audio for ID 1412...
  Generating English audio for ID 1415...
  Generating Chinese audio for ID 1415...
  Generating English audio for ID 1419...
  Generatin